In [ ]:
# get candidate genes for screening with zebrafish crispants

In [2]:
library(ggplot2)
library(viridis)
library(dplyr)

In [3]:
# load data, remove some genes
df1 = read.delim('human_CHD_case_genes_summary.csv', sep = ',')
df1$pLI = as.numeric(df1$pLI)
df1$mouse_exp_rank = as.numeric(df1$mouse_exp_rank)

df1 <- df1[which(df1$LoF>0 | df1$DMis>0),]
df1 <- df1[which(df1$known_CHD==0),]
dim(df1)
df1[1,]

Warning message in eval(expr, envir, enclos):
“NAs introduced by coercion”
Warning message in eval(expr, envir, enclos):
“NAs introduced by coercion”


[1] 7309   21

Gene   LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ extracardiac neuro pLI 
1 MARCH9 1   0    0   0   0   0   0       1     0    ⋯ 0            1     0.35
  mouse_exp_rank known_CHD CHD_DEG Disease CM_DEG TF chromatin_modifier
1 36.2           0         0       NA      0      0  0

In [4]:
# another om - TAGR
load('~/orthologs/20200625_tagr_nodups.Rdata')
cols1 = c('Gene1SpeciesName', 'Gene2SpeciesName', 'Gene1Symbol', 'Gene2Symbol', 'mean_spec')
oa1 = oa.mat[which(oa.mat$Gene1SpeciesName=='Homo sapiens' & oa.mat$Gene2SpeciesName=='Danio rerio'), cols1]
oa2 = oa.mat[which(oa.mat$Gene2SpeciesName=='Homo sapiens' & oa.mat$Gene1SpeciesName=='Danio rerio'), cols1]
oa2 <- oa2[,c(2,1,4,3,5)]
colnames(oa2) = cols1

oa3 = rbind(oa1, oa2)
oa3[1,]

Gene1SpeciesName Gene2SpeciesName Gene1Symbol Gene2Symbol mean_spec
124578 Homo sapiens     Danio rerio      DUPD1       dupd1       NA

In [5]:
# for each human gene, add all orthologs and summary stats
df2 = c()

for(ii in 1:dim(df1)[1]){
    currgene = df1$Gene[ii]
    ids = which(oa3$Gene1Symbol==currgene)
    
    if(length(ids)>0){
        temp = data.frame(zebrafish_gene = oa3$Gene2Symbol[ids])
        
        if(length(ids)==1){
            temp$orthology_type = 'ortholog_one2one'
        }else{
            temp$orthology_type = 'ortholog_one2many'
        }

        temp$coexp_cons = oa3$mean_spec[ids]
    }else{
        temp = data.frame(zebrafish_gene = NA, orthology_type = NA, coexp_cons = NA)
    }

    temp2 = df1[ii,]
    temp2[rep(seq_len(nrow(temp2)), each = dim(temp)[1]), ]
    rownames(temp2) = NULL
    df2 = rbind(df2, cbind(temp2, temp))
}
dim(df2)
df2[1,]

[1] 9475   24

Gene   LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ mouse_exp_rank known_CHD
1 MARCH9 1   0    0   0   0   0   0       1     0    ⋯ 36.2           0        
  CHD_DEG Disease CM_DEG TF chromatin_modifier zebrafish_gene orthology_type
1 0       NA      0      0  0                  NA             NA            
  coexp_cons
1 NA

In [6]:
# how many have 1-1 ortholog?
om = read.delim('human_zebrafish_ensembl_orthologs.txt', sep = '\t')
om <- om[om[,1]!='' & om[,2]!='',]
colnames(om) = c('human', 'zebrafish', 'homology_type', 'pct1', 'pct2', 'conf')
om$seq_sim = 0.5*(om$pct1 + om$pct2)

dim(om)
om[1,]
table(om$homology_type)

[1] 17698     7

human  zebrafish homology_type    pct1    pct2    conf seq_sim 
6 MT-ND1 mt-nd1    ortholog_one2one 66.3522 65.1235 1    65.73785


ortholog_many2many  ortholog_one2many   ortholog_one2one 
              3024               5786               8888 

In [7]:
# for each human gene, add all orthologs and summary stats
df2$seq_sim = NA

for(ii in 1:dim(df2)[1]){
    g1 = df2$Gene[ii]
    g2 = df2$zebrafish_gene[ii]
    id = which(om$human==g1 & om$zebrafish==g2)

    if(length(id)){       
        df2$seq_sim[ii] = om$seq_sim[id]
    }   
}
dim(df2)
df2[1,]

Warning message in df2$seq_sim[ii] <- om$seq_sim[id]:
“number of items to replace is not a multiple of replacement length”
Warning message in df2$seq_sim[ii] <- om$seq_sim[id]:
“number of items to replace is not a multiple of replacement length”


[1] 9475   25

Gene   LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ known_CHD CHD_DEG
1 MARCH9 1   0    0   0   0   0   0       1     0    ⋯ 0         0      
  Disease CM_DEG TF chromatin_modifier zebrafish_gene orthology_type coexp_cons
1 NA      0      0  0                  NA             NA             NA        
  seq_sim
1 NA

In [8]:
sum(is.na(df2$zebrafish_gene))
df3 <- df2[!is.na(df2$zebrafish_gene),]
df3[1,]

[1] 1762

Gene  LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ known_CHD CHD_DEG Disease
7 NUMBL 1   0    0   0   0   0   0       1     0    ⋯ 0         0       NA     
  CM_DEG TF chromatin_modifier zebrafish_gene orthology_type   coexp_cons
7 0      0  0                  numbl          ortholog_one2one 0.8596637 
  seq_sim 
7 58.84585

In [9]:
# add pseudobulk exp across hpf 3.3-24 from TOME
pb = read.delim('~/Atlas/TOME/saturn/zebrafish_pseudobulk_expression.csv', sep = ',')
dim(pb)
pb[c('tbx5a', 'tnnt2a'),]

[1] 30032    32

Neural.crest Optic     Eye.primordium Neuroectoderm Notoplate Neuron    
tbx5a  9.4835194    5.1434627 12.1351608     15.1675589    11.20049  10.7608284
tnnt2a 0.7527102    0.4535532  0.6330188      0.4151261     0.00000   0.7388042
       Rohon.beard.neuron Forebrain.midbrain Hindbrain Non.neural.ectoderm ⋯
tbx5a  9.7252610          8.2942488          8.2783828 13.2187311          ⋯
tnnt2a 0.5728821          0.8003966          0.3476496  0.2353191          ⋯
       Pronephric.mesenchyme Blood     Macrophage Endothelial
tbx5a  18.68849               4.799272  2.29308   6.407633   
tnnt2a  0.00000              13.969236 16.53422   6.042488   
       Dorsal.Spemann.organizer Notochord  Hatching.gland
tbx5a  11.6735                  15.6338609 3.414127      
tnnt2a  0.0000                   0.6951652 8.254140      
       Involuting.marginal.zone Endoderm Blastula  
tbx5a  12.9660008               13.44347 11.2096632
tnnt2a  0.4953366                1.37169  0.2180156

In [10]:
df3$heart_exp = pb$Heart[match(df3$zebrafish_gene, rownames(pb))]
df3$skeletal_exp = pb$Skeletal.muscle[match(df3$zebrafish_gene, rownames(pb))]
df3[1:2,]

Gene  LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ Disease CM_DEG TF
7 NUMBL 1   0    0   0   0   0   0       1     0    ⋯ NA      0      0 
9 A2M   2   0    1   0   0   0   0       1     0    ⋯ NA      0      0 
  chromatin_modifier zebrafish_gene  orthology_type    coexp_cons seq_sim 
7 0                  numbl           ortholog_one2one  0.8596637  58.84585
9 0                  si:dkey-46g23.2 ortholog_one2many 0.5281536        NA
  heart_exp skeletal_exp
7 2.4131649 4.218253    
9 0.9232356 2.087184

In [11]:
# load another CM-specific exp data
exp1 = read.delim('GSE115263_ZF_CM_FPKM_Table.txt', sep = '\t')
exp1 <- exp1[,-c(1,13)]
exp1[1:2,]

symbol           group3_1 group3_3 group3_2 group2_1 group2_2 group2_3
1 AC024175.17      41895.2      0.0  35142.60 52890.4  49939.80 43772.4 
2 si:dkeyp-3b12.11 29247.6  14757.5   2779.05 25739.9   8377.59 18740.3 
  group1_2 group1_3 group1_1 Average_FPKM
1 28919.50 52410.5  26894.3  36873.86    
2  6671.32 14758.3  32974.9  17116.27

In [12]:
df3$CM_exp = exp1$Average_FPKM[match(df3$zebrafish_gene, exp1$symbol)]
df3[1:2,]

Gene  LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ CM_DEG TF
7 NUMBL 1   0    0   0   0   0   0       1     0    ⋯ 0      0 
9 A2M   2   0    1   0   0   0   0       1     0    ⋯ 0      0 
  chromatin_modifier zebrafish_gene  orthology_type    coexp_cons seq_sim 
7 0                  numbl           ortholog_one2one  0.8596637  58.84585
9 0                  si:dkey-46g23.2 ortholog_one2many 0.5281536        NA
  heart_exp skeletal_exp CM_exp  
7 2.4131649 4.218253     5.924463
9 0.9232356 2.087184           NA

In [14]:
table(df3$orthology_type)
length(unique(df3$Gene))


ortholog_one2many  ortholog_one2one 
             3457              4256 

[1] 5546

In [17]:
# shortlist with stringent thresholds for 1-many orthologs
list1 = unique(df3$Gene[df3$orthology_type=='ortholog_one2many'])
one2many = c()

for(ii in 1:length(list1)){
    temp = df3[df3$Gene==list1[ii],]

    ids = which(!is.na(temp$heart_exp) & (temp$heart_exp>temp$skeletal_exp)
                & temp$heart_exp>=5 & !is.na(temp$CM_exp) & temp$CM_exp>=5)

    if(length(ids)==1){
        one2many = rbind(one2many, temp[ids,])
    }else if(length(ids)>1){
        one2many = rbind(one2many, temp[ids[which.max(temp$CM_exp[ids])],])
    }
}

length(list1)
dim(one2many)

[1] 1290

[1] 343  28

In [18]:
# new data.frame with one zebrafish ortholog per gene, and expressed in heart + CM
id1 = which(df3$orthology_type=='ortholog_one2one' & !is.na(df3$heart_exp) & (df3$heart_exp>df3$skeletal_exp)
            & df3$heart_exp>=5 & !is.na(df3$CM_exp) & df3$CM_exp>=5)
length(id1)

df4 = rbind(df3[id1,], one2many)
df4$heart_exp_enrichment = log2(df4$heart_exp/df4$skeletal_exp)
dim(df4)
df4[1,]

[1] 1063

[1] 1406   29

Gene LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ TF chromatin_modifier
22 AAR2 2   0    1   0   0   0   0       1     0    ⋯ 0  0                 
   zebrafish_gene orthology_type   coexp_cons seq_sim heart_exp skeletal_exp
22 aar2           ortholog_one2one 0.9749698  60.9375 16.81951  14.82708    
   CM_exp   heart_exp_enrichment
22 5.062844 0.181901

In [19]:
df5 = df4 %>% arrange(desc(pLI), desc(heart_exp_enrichment), desc(CM_exp), desc(CHD_DEG), desc(CM_DEG),
                      desc(TF), desc(mouse_exp_rank))
head(df5, n = 2)

Gene     LoF DMis LVO HTX AVC CTD CTD_TGA other none ⋯ TF chromatin_modifier
1 ATP2A2   2   1    1   0   0   0   0       2     0    ⋯ 0  0                 
2 ARHGAP29 2   0    1   0   0   0   0       1     0    ⋯ 0  0                 
  zebrafish_gene orthology_type    coexp_cons seq_sim heart_exp skeletal_exp
1 atp2a2a        ortholog_one2many 0.9566465  NA      107.98642 4.810532    
2 arhgap29a      ortholog_one2many 0.9297096  NA       51.68867 3.316310    
  CM_exp    heart_exp_enrichment
1 723.18322 4.488510            
2  25.29384 3.962197

In [21]:
table(df5$cardiac)
length(unique(df5$Gene))


  LVO other 
  322  1084 

[1] 1406

In [342]:
# subset to interesting genes
cols2 = c('Gene', 'LoF', 'DMis', 'cardiac', 'extracardiac', 'neuro', 'pLI', 'CHD_DEG', 'Disease', 'CM_DEG',
          'TF', 'chromatin_modifier', 'mouse_exp_rank', 'zebrafish_gene', 'coexp_cons', 'seq_sim', 'heart_exp',
          'skeletal_exp', 'CM_exp', 'heart_exp_enrichment')

df6 = df5[,cols2]
df6$num_mutations = as.numeric(df6$LoF) + as.numeric(df6$DMis)
df6 <- df6[which(df6$heart_exp_enrichment>1),]
dim(df6)

[1] 768  21

In [359]:
# shorten further
g0 = df6$Gene[which(df6$CHD_DEG==1 | df6$pLI>0.9 | df6$CM_DEG==1 | df6$TF==1 | df6$chromatin_modifier==1 |
                   df6$num_mutations>2)]

length(g0)

temp = df6[match(g0, df6$Gene),]
temp$pLI_score = 0
temp$pLI_score[temp$pLI>0.9] = 1

[1] 334

In [352]:
# re-order
df7 = temp %>% arrange(desc(pLI_score), desc(CHD_DEG), desc(CM_DEG), desc(TF), desc(chromatin_modifier),
                desc(heart_exp_enrichment), desc(CM_exp), desc(num_mutations), desc(mouse_exp_rank))
head(df7, n = 2)

Gene   LoF DMis cardiac extracardiac neuro pLI  CHD_DEG Disease              
1 CBLB   2   0    LVO     0.5          0.5   0.91 1       HLHS_fail TOF        
2 FNDC3B 1   0    other   0            0.5   1.00 1       DCM HCM HLHS_fail TOF
  CM_DEG ⋯ mouse_exp_rank zebrafish_gene coexp_cons seq_sim heart_exp
1 1      ⋯ 71.7           cblb           0.7141338       NA 11.25590 
2 1      ⋯ 88.9           fndc3ba        0.8134277  67.8305 74.26129 
  skeletal_exp CM_exp   heart_exp_enrichment num_mutations pLI_score
1  1.589188    14.69701 2.824320             2             1        
2 13.371346    36.02381 2.473466             1             1

In [353]:
write.table(df7[,-7], file = 'zebrafish_candidates_subset.csv', sep = ',', row.names = F,
           col.names = T, quote = F)

In [22]:
# coexp cons?
df7 = read.delim('zebrafish_candidates_subset.csv', sep = ',')
df7[1,]

Gene LoF DMis cardiac extracardiac neuro CHD_DEG Disease       CM_DEG TF ⋯
1 CBLB 2   0    LVO     0.5          0.5   1       HLHS_fail TOF 1      0  ⋯
  mouse_exp_rank zebrafish_gene coexp_cons seq_sim heart_exp skeletal_exp
1 71.7           cblb           0.7141338  NA      11.2559   1.589188    
  CM_exp   heart_exp_enrichment num_mutations pLI_score
1 14.69701 2.82432              2             1

In [24]:
temp = df7[(df7$coexp_cons>0.9 & !is.na(df7$coexp_cons)),]
dim(temp)
sum(temp$TF)
sum(temp$CHD_DEG)
sum(temp$CM_DEG)
sum(temp$pLI)

[1] 153  21

[1] 18

[1] 19

[1] 9

[1] 94

In [360]:
# CM3 - disease CMs
deg3 = read.delim('DEG_CM.csv', sep = ',')
deg3 <- deg3[deg3$cluster!='CM3',]
deg3[1,]

p_val avg_log2FC pct.1 pct.2 p_val_adj cluster gene        
1 0     1.805465   0.85  0.341 0         CM1     CTD-3179P9.1

In [366]:
# shorten further
g0 = df6$Gene[which(df6$CHD_DEG==1 | df6$pLI>0.9 | df6$CM_DEG==1 | df6$TF==1 | df6$chromatin_modifier==1)]

length(g0)

temp2 = df6[match(g0, df6$Gene),]


sum(!is.na(match(temp2$Gene, deg3$gene)))
temp2$cluster = deg3$cluster[match(temp2$Gene, deg3$gene)]

[1] 258

[1] 11

In [365]:
temp2 <- temp2[!is.na(temp2$cluster),]
temp2

Gene     LoF DMis cardiac extracardiac      neuro     pLI  CHD_DEG
7    IQGAP1   1   1    LVO     0                 0.3333333 1.00 0      
35   SORT1    1   0    other   0                 0.0000000 1.00 1      
40   AGO2     0   1    other   1                 1.0000000 1.00 1      
90   DLG1     1   0    other   1                 1.0000000 1.00 0      
94   HIPK2    1   0    other   1                 1.0000000 1.00 0      
101  ASAP1    1   0    other   1                 0.0000000 1.00 0      
257  SMC5     3   0    other   0.666666666666667 0.3333333 0.98 0      
261  PTPRK    3   0    other   0.666666666666667 0.0000000 0.98 0      
276  MAPRE2   2   0    LVO     0.666666666666667 0.3333333 0.97 0      
445  CDC14B   1   0    other   0                 0.0000000 0.58 1      
518  RRAD     1   1    LVO     0                 0.0000000 0.31 0      
532  MYL6     1   0    other   0                 0.0000000 0.26 0      
546  ACTG1    0   1    other   0                 0.0000000 0.22 0      
587  MYLK3    2   0    LVO     0.5               0.5000000 0.14 0      
610  IFRD1    1   0    other   1                 0.0000000 0.11 0      
611  FGF12    0   1    other   0                 0.0000000 0.11 0      
643  MYL9     1   0    other   0                 0.0000000 0.07 0      
750  TNNT2    1   0    other   1                 0.0000000 0.01 0      
858  ANXA11   1   0    other   1                 0.0000000 0.00 0      
866  EMILIN2  1   0    other   0                 0.0000000 0.00 1      
871  CPVL     3   0    other   0                 0.6666667 0.00 0      
884  CAST     1   0    other   0                 0.0000000 0.00 0      
908  PPP1R13L 1   0    other   0                 1.0000000 0.00 0      
934  RGS3     1   0    other   1                 1.0000000 0.00 0      
935  NMRK2    1   0    other   0                 0.0000000 0.00 0      
1057 DCP1B    2   0    LVO     1                 0.5000000 0.00 0      
     Disease      CM_DEG ⋯ mouse_exp_rank zebrafish_gene coexp_cons seq_sim 
7    NA           0      ⋯  86.2          iqgap1         0.9199091  77.05315
35   HCM          0      ⋯  93.5          sort1a         0.9758747  61.24515
40   HLHS_DN-HLHS 0      ⋯  74.9          ago2           0.9312525  90.76805
90   NA           0      ⋯  79.2          dlg1           0.7697329        NA
94   NA           0      ⋯  66.7          hipk2          0.9804537  79.74190
101  NA           0      ⋯  70.8          asap1b         0.6993195        NA
257  NA           0      ⋯  67.4          smc5           0.8873499  48.49980
261  NA           0      ⋯  90.5          ptprk                 NA        NA
276  NA           0      ⋯  96.8          mapre2         0.6599686  72.58680
445  HLHS_DN-HLHS 0      ⋯  70.5          cdc14b         0.7783036  52.79900
518  NA           0      ⋯  97.7          rrad           0.7356199  66.45885
532  NA           0      ⋯  98.4          zgc:153867     0.9597527  60.89040
546  NA           0      ⋯  99.2          actb2          0.9195426  98.66670
587  NA           0      ⋯  95.1          mylk3          0.7483081  37.17060
610  NA           0      ⋯  62.2          ifrd1          0.7827138  61.77735
611  NA           0      ⋯  53.2          fgf12b         0.9044249  82.20060
643  NA           0      ⋯  99.9          myl9b          0.9913370  94.49355
750  NA           0      ⋯ 100.0          tnnt2a         0.9943895  64.18675
858  NA           0      ⋯  72.8          anxa11b        0.8897024  59.62025
866  HLHS_DN-HLHS 0      ⋯  94.3          emilin2b       0.6273355        NA
871  NA           0      ⋯   0.0          cpvl           0.9690483  58.07155
884  NA           0      ⋯  77.5          cast           0.9513088  24.19275
908  NA           0      ⋯  77.7          ppp1r13l       0.7177443  34.39285
934  NA           0      ⋯  89.7          rgs3b          0.3378481        NA
935  NA           0      ⋯  57.0          mibp           0.2162146        NA
1057 NA           0      ⋯  41.9          dcp1b            